In [101]:
import branca
import dask.distributed
import folium
import folium.plugins
import geopandas as gpd
import numpy as np
import rasterio as rio
import rasterio.features
import shapely.geometry
import stackstac
import xrspatial.multispectral as ms
from branca.element import Element, Figure
from odc.stac import configure_rio, stac_load
from pystac_client import Client
import rioxarray
import xarray_leaflet


from utils import convert_bounds, image_on_map

In [102]:
# start the dask cluster
client = dask.distributed.Client()
configure_rio(cloud_defaults=True, aws={"aws_unsigned": True}, client=client)
client

/home/biel/miniconda3/envs/gis/lib/python3.11/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 44027 instead
  warnings.warn(


<Client: 'tcp://127.0.0.1:46137' processes=6 threads=24, memory=31.29 GiB>

In [103]:
# paste here the bbox json
aoi = {
    "type": "Polygon",
    "coordinates": [
        [
            [2.866745, 39.104489],
            [2.866745, 39.229594],
            [3.0336, 39.229594],
            [3.0336, 39.104489],
            [2.866745, 39.104489],
        ]
    ],
}
bbox = rasterio.features.bounds(aoi)

In [104]:
catalog = Client.open("https://earth-search.aws.element84.com/v1")

query = catalog.search(
    collections=["sentinel-2-l2a"],
    datetime="2023-04-01/2023-06",  # from / to
    bbox=bbox,
    query={"eo:cloud_cover": {"lt": 25}},
)

items = list(query.get_items())
print(f"Found: {len(items)} datasets")

# Convert STAC items into a GeoJSON FeatureCollection
stac_json = query.get_all_items_as_dict()

Found: 15 datasets


In [105]:
data = (
    stackstac.stack(
        items,
        assets=["red", "green", "blue", "nir", "coastal"],  # red, green, blue
        chunksize="auto",
        resolution=10,
        bounds_latlon=bbox,
        resampling=rio.enums.Resampling.average
        # epsg=3857
    )
    # .where(lambda x: x > 0, other=np.nan)  # sentinel-2 uses 0 as nodata
    # .assign_coords(band=lambda x: x.common_name.rename("band"))  # use common names
)
data

/home/biel/miniconda3/envs/gis/lib/python3.11/site-packages/stackstac/prepare.py:363: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  times = pd.to_datetime(


<xarray.DataArray 'stackstac-b6c134d07c3efa1c98b80fc946fe87fb' (time: 15,
                                                                band: 5,
                                                                y: 1390, x: 1444)>
dask.array<fetch_raster_window, shape=(15, 5, 1390, 1444), dtype=float64, chunksize=(2, 2, 1390, 1444), chunktype=numpy.ndarray>
Coordinates: (12/52)
  * time                                     (time) datetime64[ns] 2023-04-02...
    id                                       (time) <U24 'S2A_31SED_20230402_...
  * band                                     (band) <U7 'red' ... 'coastal'
  * x                                        (x) float64 4.885e+05 ... 5.029e+05
  * y                                        (y) float64 4.342e+06 ... 4.328e+06
    s2:vegetation_percentage                 (time) float64 15.67 ... 1.899
    ...                                       ...
    raster:bands                             (band) object {'nodata': 0, 'dat...
    title                                    (band) <U30 'Red (band 4) - 10m'...
    common_name                              (band) <U7 'red' ... 'coastal'
    center_wavelength                        (band) float64 0.665 0.56 ... 0.443
    full_width_half_max                      (band) float64 0.038 ... 0.027
    epsg                                     int64 32631
Attributes:
    spec:        RasterSpec(epsg=32631, bounds=(488470, 4328370, 502910, 4342...
    crs:         epsg:32631
    transform:   | 10.00, 0.00, 488470.00|\n| 0.00,-10.00, 4342270.00|\n| 0.0...
    resolution:  10

In [106]:
selection = data[data["id"]=="S2B_31SDD_20230407_0_L2A"].squeeze("time").compute()

In [107]:
# use ms.true_color to convert RGB and improve the color
true_color = ms.true_color(
    r=selection.sel(band="nir"),
    g=selection.sel(band="red"),
    b=selection.sel(band="green"),
    nodata=-1
)
image_on_map(true_color, bbox)

In [108]:
true_color = ms.true_color(
    r=selection.sel(band="red"),
    g=selection.sel(band="green"),
    b=selection.sel(band="coastal"),
    nodata=-1,
    c=11,
    th=0.125
)
image_on_map(true_color, bbox)

In [136]:
selection.to_dataset(dim="band").reset_coords(drop=True).rio.to_raster("../data/cabrera.tif")

In [137]:
!gdalinfo ../data/cabrera.tif

Driver: GTiff/GeoTIFF
Files: ../data/cabrera.tif
Size is 1444, 1390
Coordinate System is:
PROJCRS["WGS 84 / UTM zone 31N",
    BASEGEOGCRS["WGS 84",
        DATUM["World Geodetic System 1984",
            ELLIPSOID["WGS 84",6378137,298.257223563,
                LENGTHUNIT["metre",1]]],
        PRIMEM["Greenwich",0,
            ANGLEUNIT["degree",0.0174532925199433]],
        ID["EPSG",4326]],
    CONVERSION["UTM zone 31N",
        METHOD["Transverse Mercator",
            ID["EPSG",9807]],
        PARAMETER["Latitude of natural origin",0,
            ANGLEUNIT["degree",0.0174532925199433],
            ID["EPSG",8801]],
        PARAMETER["Longitude of natural origin",3,
            ANGLEUNIT["degree",0.0174532925199433],
            ID["EPSG",8802]],
        PARAMETER["Scale factor at natural origin",0.9996,
            SCALEUNIT["unity",1],
            ID["EPSG",8805]],
        PARAMETER["False easting",500000,
            LENGTHUNIT["metre",1],
            ID["EPSG",8806]],
        P